In [1]:
%load_ext autoreload
%autoreload 2

In [2]:
from __future__ import print_function

import lightgbm as lgb
import numpy as np
import pandas as pd
import csv
import os

import sdss_gz_data as sgd
from sdss_gz_data import SPIRIAL_GALAXY_TYPE
from sdss_gz_data import ELLIPTICAL_GALAXY_TYPE
from sdss_gz_data import UNKNOWN_GALAXY_TYPE

/Users/will/Development/Astronomy/proposal/ENV/lib/python3.7/site-packages/lightgbm/__init__.py:46: UserWarning: Starting from version 2.2.1, the library file in distribution wheels for macOS is built by the Apple Clang (Xcode_8.3.3) compiler.
This means that in case of installing LightGBM from PyPI via the ``pip install lightgbm`` command, you don't need to install the gcc compiler anymore.
Instead of that, you need to install the OpenMP library, which is required for running LightGBM on the system with the Apple Clang compiler.
You can install the OpenMP library by the following command: ``brew install libomp``.
  "You can install the OpenMP library by the following command: ``brew install libomp``.", UserWarning)


In [3]:
orig_data = sgd.load_data('data/astromonical_data.csv.gz')

In [4]:
print(f'Length of data: {len(orig_data)}')
df = sgd.prepare_data(orig_data)
print(f'Length after prepared data: {len(df)}')

df = df[df.galaxy_type != UNKNOWN_GALAXY_TYPE]
print(f'Length of known galaxy types: {len(df)}')

Length of data: 537064
Filtered out 3501 invalid records
Number of high z galaxies = 231
% elliptical:      0.13576908942272356
% spiral:          0.2237143092857732
% unknown:         0.6405166012915032
% spiral of known: 0.6223216707350149
Length after prepared data: 533332
Length of known galaxy types: 191724


In [12]:
features = ['objid','run','rerun','camcol','field','obj','ra','dec','petroRad_r']

transformed_data = sgd.transform_data(df)
X = transformed_data[features]
y = transformed_data[['galaxy_type','z']]

X_train, X_test, _, _ = sgd.split_train(X, y, test_size=0.2, random_state=42)

data = X

del X, y

[ 1  2  3  4  5  6  7  8  9 10 11 12 13 14 15 16 17 18 19 25 26 27 28 29
 30 31 32 33 34 35 36 37 38 39 40 41 42 43 44 45 46 47]
Min z:             -0.0035549390000000004
Max z:             0.3936197


In [13]:
len(X_train), len(X_test)

(153379, 38345)

In [14]:
def is_train_record(record):
    series = X_train[X_train.objid == record.objid]
    return len(series) == 1

In [15]:
bucket = sgd.get_gcs_bucket()

/Users/will/Development/Astronomy/proposal/ENV/lib/python3.7/site-packages/google/auth/_default.py:66: UserWarning: Your application has authenticated using end user credentials from Google Cloud SDK. We recommend that most server applications use service accounts instead. If your application continues to use end user credentials from Cloud SDK, you might receive a "quota exceeded" or "API not enabled" error. For more information about service accounts, see https://cloud.google.com/docs/authentication/
  warnings.warn(_CLOUD_SDK_CREDENTIALS_WARNING)
/Users/will/Development/Astronomy/proposal/ENV/lib/python3.7/site-packages/google/auth/_default.py:66: UserWarning: Your application has authenticated using end user credentials from Google Cloud SDK. We recommend that most server applications use service accounts instead. If your application continues to use end user credentials from Cloud SDK, you might receive a "quota exceeded" or "API not enabled" error. For more information about serv

In [16]:
def move_incorrect_blob(incorrect_blob, new_blob_name):
    bucket.copy_blob(incorrect_blob, bucket, new_blob_name)
    
    # need to delete blob
    incorrect_blob.delete()

In [ ]:
# incorrect_blob = bucket.blob('fits/2986/4/258//tmp/2986-4-258/obj-1237658299533492319.fits.bz2')
# correct_blob_name = 'fits/2986/4/258/obj-1237658299533492319.fits.bz2'

# move_incorrect_blob(incorrect_blob, correct_blob_name)

In [11]:
from google.cloud import pubsub

PROJECT = 'astroml-ast80014'
TOPIC_NAME = 'cutout-fits-image'
TOPIC = f'projects/{PROJECT}/topics/{TOPIC_NAME}'
BUCKET = 'wgauvin-astroml-ast80014'

In [24]:
publisher = pubsub.PublisherClient()
count = 0
total = 0

def generate_message(row):
    message = {
        'run': row.run,
        'camcol': row.camcol,
        'field': row.field,
        'objects':[
            {
                'objid': row.objid,
                'ra': row.ra,
                'dec': row.dec,
                'petroRad_r': row.petroRad_r
            }
        ]
    }

    return message

def republish_message(row):
    message = generate_message(row)
    publish_message(message)
    
def publish_message(message):
    import json

    global count
    count += 1
    if count % 100 == 0:
        print(f'Sent {count}')

    msg = json.dumps(message).encode("utf-8")
    print(f'Sending message: {message}')
    publisher.publish(TOPIC, msg)


/Users/will/Development/Astronomy/proposal/ENV/lib/python3.7/site-packages/google/auth/_default.py:66: UserWarning: Your application has authenticated using end user credentials from Google Cloud SDK. We recommend that most server applications use service accounts instead. If your application continues to use end user credentials from Cloud SDK, you might receive a "quota exceeded" or "API not enabled" error. For more information about service accounts, see https://cloud.google.com/docs/authentication/
  warnings.warn(_CLOUD_SDK_CREDENTIALS_WARNING)


In [26]:
import time

def get_blob_path(record):
    return f'fits/{record.run}/{record.camcol}/{record.field}/obj-{record.objid}.fits.bz2'

def get_alternative_blob_path(record):
    return f'fits/{record.run}/{record.camcol}/{record.field}//tmp/{record.run}-{record.camcol}-{record.field}/obj-{record.objid}.fits.bz2'

start = time.time()
chunck_start = time.time()

total_count = 0
moved_count = 0

dfs = {
    'train': {
        'exists': pd.DataFrame(columns=features),
        'not_exists': pd.DataFrame(columns=features)
    },
    'test': {
        'exists': pd.DataFrame(columns=features),
        'not_exists': pd.DataFrame(columns=features)
    }
}

def report_counts():
    num_train_exists = len(dfs['train']['exists'])
    num_train_not_exists = len(dfs['train']['not_exists'])
    num_test_exists = len(dfs['test']['exists'])
    num_test_not_exists = len(dfs['test']['not_exists'])
    total_exists = num_test_exists + num_train_exists
    total_not_exists = num_test_not_exists + num_train_not_exists
    total = total_exists + total_not_exists
    
    percent_test_to_total_exists = np.round(100.0 * num_test_exists / (total_exists + 1.0e-6), 2)
    percent_moved_to_exists = np.round(100.0 * moved_count / (total_exists + 1.0e-6), 2)
    percent_exists = np.round(100.0 * total_exists / total, 2)
    
    print('')
    print('Exists:')
    print(f'train: {num_train_exists}')
    print(f'test : {num_test_exists}')
    print('')
    print('Not exist')
    print(f'train: {num_train_not_exists}')
    print(f'test : {num_test_not_exists}')
    print('')
    print('Percentages')
    print(f'Test of Exist: {percent_test_to_total_exists}')
    print(f'That exists  : {percent_exists}')
    print(f'Moved Exists : {percent_moved_to_exists}')
    print('')
    print('Totals:')
    print(f'exists    : {total_exists}')
    print(f'moved     : {moved_count}')
    print(f'not_exists: {total_not_exists}')
    print(f'total     : {total}')

def get_blob_state(record):
    global moved_count

    blob_path = get_blob_path(record)
    blob = bucket.blob(blob_path)
    if blob.exists():
        return 'exists'
    else:
        incorrect_blob_path = get_alternative_blob_path(record)
        incorrect_blob = bucket.blob(incorrect_blob_path)
        if (incorrect_blob.exists()):
            move_incorrect_blob(incorrect_blob, blob_path)
            moved_count += 1
            return 'exists'

        return 'not_exists'

def handle_record(record):
    def append_row(df):
        return df.append(record._asdict(), ignore_index=True)

    def get_record_type_dfs(record):
        if is_train_record(record):
            return dfs['train']
        else:
            return dfs['test']

    type_dfs = get_record_type_dfs(record)
    state = get_blob_state(record)
    type_dfs[state] = append_row(type_dfs[state])

    if state == 'not_exists':
        republish_message(record)
        
    return state

for record in data.itertuples():
    state = handle_record(record)

    total_count += 1

    if (total_count % 1000 == 0):
        end = time.time()
        report_counts()
        print(f'Total checked = {total_count}. Took {(end - chunck_start):0.3f} seconds')

report_counts()
end = time.time()


Exists:
train: 795
test : 205

Not exist
train: 0
test : 0

Percentages
Test of Exist: 20.5
That exists  : 100.0
Moved Exists : 0.0

Totals:
exists    : 1000
moved     : 0
not_exists: 0
total     : 1000
Total checked = 1000. Took 171.537 seconds

Exists:
train: 1574
test : 426

Not exist
train: 0
test : 0

Percentages
Test of Exist: 21.3
That exists  : 100.0
Moved Exists : 0.0

Totals:
exists    : 2000
moved     : 0
not_exists: 0
total     : 2000
Total checked = 2000. Took 438.583 seconds
Sending message: {'run': 756, 'camcol': 3, 'field': 624, 'objects': [{'objid': '1237648721243537600', 'ra': 209.229747123074, 'dec': -0.171214343288909, 'petroRad_r': 1.6153398616176322}]}
Sending message: {'run': 752, 'camcol': 1, 'field': 395, 'objects': [{'objid': '1237648702974918784', 'ra': 202.686080350223, 'dec': -1.1580786428757701, 'petroRad_r': 1.3616706711543005}]}
Sending message: {'run': 1331, 'camcol': 5, 'field': 240, 'objects': [{'objid': '1237651191898308806', 'ra': 140.66253320581, 

Sending message: {'run': 1045, 'camcol': 6, 'field': 109, 'objects': [{'objid': '1237649964065947702', 'ra': 50.2532775995707, 'dec': -5.97538616357713, 'petroRad_r': 1.5632123867661136}]}
Sending message: {'run': 1231, 'camcol': 1, 'field': 19, 'objects': [{'objid': '1237650760239612081', 'ra': 172.08369168239702, 'dec': -3.6218599995247502, 'petroRad_r': 1.8285742455633003}]}
Sending message: {'run': 756, 'camcol': 6, 'field': 425, 'objects': [{'objid': '1237648722841108622', 'ra': 179.402560827836, 'dec': 1.1407747578696499, 'petroRad_r': 2.3652593775218667}]}
Sending message: {'run': 1302, 'camcol': 6, 'field': 361, 'objects': [{'objid': '1237651067889057949', 'ra': 179.446072505335, 'dec': 66.1124751801792, 'petroRad_r': 1.5735027080809814}]}
Sending message: {'run': 756, 'camcol': 3, 'field': 654, 'objects': [{'objid': '1237648721245503722', 'ra': 213.736195624508, 'dec': -0.035900277773812994, 'petroRad_r': 1.6176151872034046}]}
Sending message: {'run': 756, 'camcol': 5, 'field'

Sending message: {'run': 1239, 'camcol': 5, 'field': 172, 'objects': [{'objid': '1237650796756861130', 'ra': 146.15185862512502, 'dec': 0.613467186373361, 'petroRad_r': 1.6130750898775195}]}
Sending message: {'run': 1302, 'camcol': 6, 'field': 429, 'objects': [{'objid': '1237651067893514407', 'ra': 204.014840320952, 'dec': 64.9161353887473, 'petroRad_r': 1.442678475267188}]}
Sending message: {'run': 1045, 'camcol': 4, 'field': 116, 'objects': [{'objid': '1237649962992664710', 'ra': 51.364486451469496, 'dec': -6.643958624886269, 'petroRad_r': 1.357490741156416}]}
Sending message: {'run': 756, 'camcol': 3, 'field': 387, 'objects': [{'objid': '1237648721228005435', 'ra': 173.81633831287, 'dec': -0.0448937434144341, 'petroRad_r': 1.5624003914878586}]}
Sending message: {'run': 1140, 'camcol': 6, 'field': 197, 'objects': [{'objid': '1237650372093608132', 'ra': 182.464975161699, 'dec': -1.4032833643076297, 'petroRad_r': 1.4779175249540142}]}
Sending message: {'run': 1140, 'camcol': 1, 'field'

Sending message: {'run': 756, 'camcol': 1, 'field': 764, 'objects': [{'objid': '1237648720178970774', 'ra': 230.158056592462, 'dec': -0.937875197181838, 'petroRad_r': 1.5745969541369136}]}
Sending message: {'run': 1035, 'camcol': 2, 'field': 169, 'objects': [{'objid': '1237649918972723418', 'ra': 31.308162564259, 'dec': 12.7492831662961, 'petroRad_r': 1.4830135478076354}]}
Sending message: {'run': 1339, 'camcol': 3, 'field': 37, 'objects': [{'objid': '1237651225171001538', 'ra': 255.706100915819, 'dec': 60.9681838152021, 'petroRad_r': 1.954301698454389}]}
Sending message: {'run': 1339, 'camcol': 3, 'field': 40, 'objects': [{'objid': '1237651225171198270', 'ra': 255.937350200456, 'dec': 60.5125304305318, 'petroRad_r': 1.8418744696999019}]}
Sending message: {'run': 1345, 'camcol': 5, 'field': 563, 'objects': [{'objid': '1237651252049019039', 'ra': 239.781832979745, 'dec': 52.209079281187, 'petroRad_r': 1.8309335466785241}]}
Sending message: {'run': 1345, 'camcol': 3, 'field': 78, 'object

Sending message: {'run': 1345, 'camcol': 4, 'field': 419, 'objects': [{'objid': '1237651251502711009', 'ra': 204.944853078736, 'dec': 64.02845896641989, 'petroRad_r': 1.472847216337811}]}
Sending message: {'run': 1350, 'camcol': 1, 'field': 420, 'objects': [{'objid': '1237651271367000252', 'ra': 203.483965489128, 'dec': 65.20403115955901, 'petroRad_r': 1.6162329736256198}]}
Sending message: {'run': 1231, 'camcol': 2, 'field': 109, 'objects': [{'objid': '1237650760782381157', 'ra': 185.518349863569, 'dec': -3.17885130032566, 'petroRad_r': 1.2822424333318088}]}
Sending message: {'run': 1350, 'camcol': 2, 'field': 233, 'objects': [{'objid': '1237651271891615831', 'ra': 141.745357738846, 'dec': 59.31693627481361, 'petroRad_r': 1.6750707720648175}]}
Sending message: {'run': 1231, 'camcol': 3, 'field': 185, 'objects': [{'objid': '1237650761324232787', 'ra': 196.901471416193, 'dec': -2.82017910832606, 'petroRad_r': 2.621521616640419}]}
Sending message: {'run': 1239, 'camcol': 3, 'field': 134,

...

Sending message: {'run': 5061, 'camcol': 4, 'field': 268, 'objects': [{'objid': '1237667211591286910', 'ra': 154.297000309618, 'dec': 26.6038485912075, 'petroRad_r': 1.7195000182750204}]}
Sending message: {'run': 5061, 'camcol': 4, 'field': 347, 'objects': [{'objid': '1237667211596464166', 'ra': 167.423611834324, 'dec': 28.915004602445396, 'petroRad_r': 2.173219184112073}]}
Sending message: {'run': 5116, 'camcol': 6, 'field': 75, 'objects': [{'objid': '1237667448875581527', 'ra': 180.4909242408, 'dec': 26.0335423679625, 'petroRad_r': 1.6026638199908954}]}
Sending message: {'run': 5116, 'camcol': 6, 'field': 138, 'objects': [{'objid': '1237667448879710348', 'ra': 191.013299087667, 'dec': 26.007164404011, 'petroRad_r': 2.131442972779391}]}
Sending message: {'run': 4649, 'camcol': 2, 'field': 332, 'objects': [{'objid': '1237665440995213459', 'ra': 234.559933530867, 'dec': 19.689698241287697, 'petroRad_r': 2.1803371168094383}]}
Sending message: {'run': 4649, 'camcol': 3, 'field': 53, 'obje

Sending message: {'run': 4570, 'camcol': 2, 'field': 210, 'objects': [{'objid': '1237665101684801959', 'ra': 239.40016638314302, 'dec': 21.5953781225246, 'petroRad_r': 1.8865404181053036}]}
Sending message: {'run': 4570, 'camcol': 3, 'field': 42, 'objects': [{'objid': '1237665102210662568', 'ra': 213.552743506827, 'dec': 31.5693336068158, 'petroRad_r': 2.257454349968144}]}
Sending message: {'run': 4629, 'camcol': 2, 'field': 180, 'objects': [{'objid': '1237665355085906111', 'ra': 245.865843048751, 'dec': 41.7064059086854, 'petroRad_r': 2.900887935228674}]}
Sending message: {'run': 4570, 'camcol': 3, 'field': 71, 'objects': [{'objid': '1237665102212563083', 'ra': 218.30567613779, 'dec': 30.2618573745993, 'petroRad_r': 1.4312631856433244}]}
Sending message: {'run': 4629, 'camcol': 3, 'field': 201, 'objects': [{'objid': '1237665355624153423', 'ra': 245.184918639488, 'dec': 44.8269178560306, 'petroRad_r': 1.727676311063693}]}
Sending message: {'run': 5087, 'camcol': 4, 'field': 304, 'objec

Sending message: {'run': 4469, 'camcol': 6, 'field': 383, 'objects': [{'objid': '1237664670051926206', 'ra': 172.068184076605, 'dec': 40.5417692352606, 'petroRad_r': 1.6558158361562338}]}
Sending message: {'run': 4552, 'camcol': 3, 'field': 201, 'objects': [{'objid': '1237665024911671313', 'ra': 203.10845922783798, 'dec': 33.5123797620256, 'petroRad_r': 2.146092907313648}]}

Exists:
train: 80146
test : 20189

Not exist
train: 31055
test : 7610

Percentages
Test of Exist: 20.12
That exists  : 72.18
Moved Exists : 44.84

Totals:
exists    : 100335
moved     : 44994
not_exists: 38665
total     : 139000
Total checked = 139000. Took 38661.322 seconds
Sending message: {'run': 4552, 'camcol': 3, 'field': 246, 'objects': [{'objid': '1237665024914620503', 'ra': 210.94131396308998, 'dec': 32.0003821449872, 'petroRad_r': 2.068608197334979}]}
Sending message: {'run': 4470, 'camcol': 1, 'field': 121, 'objects': [{'objid': '1237664671645368493', 'ra': 204.211274971851, 'dec': 34.841530848723, 'petro

Sending message: {'run': 4504, 'camcol': 4, 'field': 106, 'objects': [{'objid': '1237664819283886199', 'ra': 172.70704068137798, 'dec': 37.1901752374711, 'petroRad_r': 1.5279241232505543}]}
Sending message: {'run': 5087, 'camcol': 4, 'field': 138, 'objects': [{'objid': '1237667323251916912', 'ra': 171.83444111141003, 'dec': 27.067356514136602, 'petroRad_r': 1.972438566812938}]}
Sending message: {'run': 4649, 'camcol': 4, 'field': 249, 'objects': [{'objid': '1237665442063515874', 'ra': 222.25703402955298, 'dec': 24.7153299427707, 'petroRad_r': 2.0692065928268075}]}
Sending message: {'run': 4649, 'camcol': 5, 'field': 50, 'objects': [{'objid': '1237665442587345000', 'ra': 189.261528257658, 'dec': 30.4159304296003, 'petroRad_r': 1.927654379044001}]}
Sending message: {'run': 4649, 'camcol': 5, 'field': 52, 'objects': [{'objid': '1237665442587476089', 'ra': 189.603203900816, 'dec': 30.431160936117102, 'petroRad_r': 1.4203092397071682}]}
Sending message: {'run': 4649, 'camcol': 5, 'field': 6

ServiceUnavailable: 503 GET https://www.googleapis.com/storage/v1/b/wgauvin-astroml-ast80014/o/fits%2F4576%2F4%2F685%2Fobj-1237665128559476910.fits.bz2?fields=name: Backend Error

In [28]:
dfs['train']['exists'].objid = dfs['train']['exists'].objid.astype(str)
dfs['train']['exists'].to_csv('train_exists.csv.bz2', index=False)

dfs['train']['not_exists'].objid = dfs['train']['not_exists'].objid.astype(str)
dfs['train']['not_exists'].to_csv('train_not_exists.csv.bz2', index=False)

dfs['test']['exists'].objid = dfs['test']['exists'].objid.astype(str)
dfs['test']['exists'].to_csv('test_exists.csv.bz2', index=False)

dfs['test']['not_exists'].objid = dfs['test']['not_exists'].objid.astype(str)
dfs['test']['not_exists'].to_csv('test_not_exists.csv.bz2', index=False)


In [29]:
total_count

139133

In [27]:
len(dfs['train']['exists']),len(dfs['train']['not_exists']),len(dfs['test']['exists']),len(dfs['test']['not_exists'])

(80210, 31095, 20205, 7623)